## 1. Required dependencies

### ***please load the packages and update the constants/variables in the cell below. after that you can run the remainder of the script to reproduce the steps I took to audit the issue. thanks!***


In [16]:
import pandas as pd
import numpy as np

# constant values needed to run script
# please update the values below

# export csv from: EDC > Flourish Caregiver > Birth Form
PATH_TO_MATERNAL_DELIVERY = '/MaternalDelivery-2024-06-20.csv'

# export csv from: EDC > Flourish Caregiver > Ultrasound Form
PATH_TO_ULTRASOUND = '/UltraSound-2024-06-14.csv'

# quick function to check df dimensions against n unique chilpid's to verify no duplicates
def print_df_dimensions(df):
    print(f"""checking dimensions:
          dimensions: {df.shape}
          nunique childpid: {df["childpid"].nunique()}
          ---------
          """)

# You can now run the rest of the script!


## 2. Run the script below to reproduce the data anomalies highlighted in this issue

### Loading data

In [19]:
# loading maternal delivery data
maternal_delivery_df = pd.read_csv(PATH_TO_MATERNAL_DELIVERY)

# verifying no duplicates
print_df_dimensions(maternal_delivery_df)

# selecting columns relevant to issue
maternal_delivery_df = maternal_delivery_df.filter(regex = "childpid|matpid|datetime")

# printing columns to confirm appropriate variables selected
print("maternal_delivery_df columns selected:\n\t", maternal_delivery_df.columns.tolist())
# renaming columns with suffix to identify CRF data was pulled from
maternal_delivery_df = maternal_delivery_df.rename(columns={"report_datetime":"report_datetime_matdeliverycrf", "delivery_datetime":"delivery_datetime_matdeliverycrf"})

print("\nnew column names for merging with ultrasound df:\n\t", maternal_delivery_df.columns.tolist())

checking dimensions:
          dimensions: (319, 34)
          nunique childpid: 319
          ---------
          
maternal_delivery_df columns selected:
	 ['matpid', 'childpid', 'report_datetime', 'delivery_datetime']

new column names for merging with ultrasound df:
	 ['matpid', 'childpid', 'report_datetime_matdeliverycrf', 'delivery_datetime_matdeliverycrf']


In [20]:
# loading ultrasound form data
ultrasound_df = pd.read_csv(PATH_TO_ULTRASOUND)

# verifying no duplicates
print_df_dimensions(ultrasound_df)

# selecting columns relevant to issue
ultrasound_df = ultrasound_df.filter(regex = "childpid|matpid|datetime|delivery_date")

# printing columns to confirm appropriate variables selected
print("ultrasound_df columns selected:\n\t", ultrasound_df.columns.tolist())
# renaming columns with suffix to identify CRF data was pulled from
ultrasound_df = ultrasound_df.rename(columns={"report_datetime":"report_datetime_ultrasoundcrf", "maternal_delivery_date":"maternal_delivery_date_ultrasoundcrf"})

print("\nnew column names for merging with maternal delivery df:\n\t", ultrasound_df.columns.tolist())

checking dimensions:
          dimensions: (351, 30)
          nunique childpid: 351
          ---------
          
ultrasound_df columns selected:
	 ['matpid', 'childpid', 'old_matpid', 'report_datetime', 'maternal_delivery_date']

new column names for merging with maternal delivery df:
	 ['matpid', 'childpid', 'old_matpid', 'report_datetime_ultrasoundcrf', 'maternal_delivery_date_ultrasoundcrf']


### Merging `maternal_delivery_df` and `ultrasound_df` on `childpid` to compare values for delivery dates across the two CRFs

In [12]:
# merging maternal_delivery_df and ultrasound_df on childpid
merged_df = pd.merge(ultrasound_df, maternal_delivery_df, on=['childpid', 'matpid'], how='left')

# verifying merge
print_df_dimensions(merged_df)


merged_df:
      dimensions: (351, 7)
      nunique childpid: 351
      ---------
      
<class 'pandas.core.frame.DataFrame'>
Index: 33 entries, 15 to 348
Data columns (total 7 columns):
 #   Column                                Non-Null Count  Dtype 
---  ------                                --------------  ----- 
 0   matpid                                33 non-null     object
 1   childpid                              33 non-null     object
 2   old_matpid                            2 non-null      object
 3   report_datetime_ultrasoundcrf         33 non-null     object
 4   maternal_delivery_date_ultrasoundcrf  33 non-null     object
 5   report_datetime_matdeliverycrf        33 non-null     object
 6   delivery_datetime_matdeliverycrf      33 non-null     object
dtypes: object(7)
memory usage: 2.1+ KB


### Creating `issue_df` with records relevant to current issue by filtering `merged_df` where:
- delivery date is not missing
- delivery date in `maternal_delivery_df` does not match/equal delivery date in `ultrasound_df`

In [ ]:
# filtering observations where delivery_datetime_matdeliverycrf does NOT equal maternal_delivery_date_ultrasoundcrf
issue_df = merged_df.copy()[~(merged_df['delivery_datetime_matdeliverycrf'] == merged_df['maternal_delivery_date_ultrasoundcrf'])]

# removing observations for subjects who haven't been born yet (i.e., where delivery date is a missing value)
issue_df = issue_df[issue_df['delivery_datetime_matdeliverycrf'].notna()]

# verifying merge
print_df_dimensions(issue_df)